<a href="https://colab.research.google.com/github/Josiah-tan/math_misc/blob/master/num_diff_integrator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Differentiation

In [27]:
import numpy as np
import plotly.graph_objects as go

from numba import njit
import sys
sys.setrecursionlimit(3500)

In [28]:
def func(x):
  y = x**2
  return y

def func2(x):
  y = x**3
  return y

In [29]:
class DataGenerator:
  def __init__(self, f = None, x_min = None, x_max = None, 
               x_num = None, x_step = None,
               x = None, y = None, data = None):
    self.f = f
    self.x_min = x_min
    self.x_max = x_max
    self.x_num = x_num
    self.x_step = x_step

    self._x = x
    self._y = y
    self._data = data

  @property
  def x(self):
    #print(self.x_num, self.x_step)
    if self._x is not None: 
      return self._x
    assert self.x_num is not None or self.x_step is not None # both self.x_num and self.x_step cannot equal None
    if self.x_num is not None:
      self._x = np.linspace(self.x_min, self.x_max, self.x_num)
    elif self.x_step is not None:
      self._x = np.arange(self.x_min, self._x_max, self.x_step)
    return self._x
  @property
  def y(self):
    if self._y is None:
      self._y = self.f(self.x)
    return self._y
  @property
  def data(self):
    if self._data is None:
      self._data = dict()
      self._data['x'] = self.x
      self._data['y'] = self.y
    return self._data

In [30]:
class ScatterPlot(DataGenerator):
  def __init__(self, *args, show_original = False, name = 'original', mode = 'lines', **kwargs):
    #print(args, kwargs)
    super().__init__(*args, **kwargs)

    self.fig = go.Figure()

    if show_original:
      self.add_data(name = name, mode = mode, **self.data)
  
  @classmethod
  def create_instance(cls, *args, **kwargs):
    #print(f"create_instance{args}, {kwargs}")
    return cls(*args, **kwargs)
  
  def add_trace(self, *args, name = 'trace', mode = 'lines', **kwargs):
    """
    add a scatterplot given only the args and kwargs of the superclass
    """
    obj = self.create_instance(*args, **kwargs)
    self.add_data(name = name, mode = mode, **obj.data)
  
  def add_data(self, **data):
    """
    add a scatterplot given that data for go.Scatter is known
    """
    self.fig.add_trace(go.Scatter(**data))
  
  def update_layout(self, *args, x_lab = '', y_lab = '', **kwargs):
    """
    kwargs: title_text
    """
    self.fig.update_layout(*args, **kwargs)
    self.fig.update_xaxes(title_text=x_lab)
    self.fig.update_yaxes(title_text=y_lab)

  def show(self):
    self.fig.show()

  

In [31]:
#testing scatterplot
x_min = 0
x_max = 1
x_num = 5
scatterplot = ScatterPlot(func, x_min, x_max, x_num, show_original = True)
print(scatterplot.x)
print(scatterplot.y)
print(scatterplot.data)
scatterplot.add_trace(func2, x_min, x_max, x_num, mode = 'markers', name = 'bob')
scatterplot.update_layout(title_text = "random graph", x_lab = 'x', y_lab = 'y')
scatterplot.show()

[0.   0.25 0.5  0.75 1.  ]
[0.     0.0625 0.25   0.5625 1.    ]
{'x': array([0.  , 0.25, 0.5 , 0.75, 1.  ]), 'y': array([0.    , 0.0625, 0.25  , 0.5625, 1.    ])}


In [32]:
class Differentiation(ScatterPlot):
  def __init__(self, *args, **kwargs):
    super().__init__(*args, **kwargs)
    self._diff_y = None

  @property
  def diff_y(self):
    if self._diff_y is None:
      self._diff_y = self(self.data)
    return self._diff_y
  
  def __call__(self, data):
    x = data['x']
    y = data['y']
    assert len(y) >= 2
    @njit
    def diff(x, y):
      diff_y = np.copy(y)
      for i in range(1, len(x)):
        dx = x[i] - x[i-1]
        dy = y[i] - y[i-1]
        diff_y[i] = dy/dx
  
      diff_y[0] = diff_y[1] # edge case
      return diff_y
    return diff(x, y)
  def show(self, name = 'diff', mode = 'markers', **kwargs):
    self.add_data(y = self.diff_y, x = self.x, name = name, mode = mode, **kwargs)
    super().show()
      
    

In [33]:
if __name__ == '__main__':
  x_min = 0
  x_max = 1
  x_num = 1000
  diff = Differentiation(func2, x_min, x_max, x_num, show_original = True, mode = 'lines')
  diff.show(mode = 'lines')

In [34]:
class Integration(ScatterPlot):
  def __init__(self, *args, meth = 'trap', const = 0, **kwargs):
    super().__init__(*args, **kwargs)
    self._int_y = None
    self.meth = {'trap' : self.trap,
                 'simp' : self.simp}.get(meth)
    self.const = const # integration constant
  @property
  def int_y(self):
    if self._int_y is None:
      self._int_y = self.meth(self.data, self.const)
    return self._int_y
  
  def trap(self, data, const):
    x = data['x']
    y = data['y']
    assert len(y) >= 2
    @njit
    def integ(x, y):
      int_y = np.copy(y)
  
      int_y[0] = const# edge case
      for i in range(1, len(x)):
        h = x[i] - x[i-1]
        w_ave = (y[i] + y[i-1]) / 2
        int_y[i] = h * w_ave + int_y[i-1]
      return int_y
    return integ(x, y)
  def simp(self, data, const):
    pass
  def show(self, name = 'int', mode = 'markers', **kwargs):
    self.add_data(y = self.int_y, x = self.x, name = name, mode = mode, **kwargs)
    super().show()
      
  

In [35]:
if __name__ == '__main__':
  x_min = 0
  x_max = 1
  x_num = 1000
  integration = Integration(func2, x_min, x_max, x_num, show_original = True, mode = 'lines')
  integration.show(mode = 'lines')

In [36]:
 
from joblib import Memory
location = './cachedir'
memory = Memory(location='./joblib_cache', verbose = 0)

@memory.cache  #@njit
def summor(x, n, go):
  assert n % 2 == 1
  if n == -1:
    return go
  go += np.sin(n * (x-1)) / n #(n * np.pi)
  n -= 2
  return summor(x, n, go)

def pulse(x):
  amplitude = 5
  n = 501
  return -4 / np.pi * summor(x, n, np.zeros_like(x)) * amplitude / 2 + amplitude / 2 #literally derived by trial and error

x_min = 0
x_max = 3/2 *np.pi
x_num = 10000
scatterplot = ScatterPlot(pulse, x_min, x_max, x_num, show_original = True, mode = 'lines')
scatterplot.update_layout(title_text = r'$V_{in} \text{ vs Time Graph Using Fourier Series}$', x_lab = 't(s)', y_lab = '$V_{in} (V)$')
scatterplot.show()

In [37]:
  diff = Differentiation(pulse, x_min, x_max, x_num, show_original = True, mode = 'lines')
  diff.show(mode = 'lines')

In [38]:
RC = 0.01
def int_pulse(x):
  diff = Differentiation(x = x, y = pulse(x))
  return np.exp(x / RC) * diff.diff_y

In [39]:
integ = Integration(int_pulse, x_min, x_max, x_num, show_original = True, mode = 'lines')
integ.show(mode = 'lines')

In [40]:
x_min = 0
x_max = 3/2 *np.pi
x_num = 10000

RC = 0.007
n = 501
amplitude = 5
@memory.cache  #@njit
def summor(x, n, go):
  assert n % 2 == 1
  if n == -1:
    return go
  go += np.sin(n * (x-1)) / n #(n * np.pi)
  n -= 2
  return summor(x, n, go)

def pulse(x):
  return -4 / np.pi * summor(x, n, np.zeros_like(x)) * amplitude / 2 + amplitude / 2 #literally derived by trial and error

def int_pulse(x):
  diff = Differentiation(x = x, y = pulse(x))
  return np.exp(x / RC) * diff.diff_y

def V_trig(x):
  integ = Integration(x = x, y = int_pulse(x))
  return amplitude + integ.int_y / np.exp(x/RC)
scatterplot2 = ScatterPlot(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
RC = 0.1
scatterplot2.add_trace(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
"""
RC *= 10
scatterplot2.add_trace(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
"""
scatterplot2.update_layout(title_text = r'$V_{TRIG} \text{ vs Time Graph}$', x_lab = 't(s)', y_lab = '$V_{TRIG} (V)$')
scatterplot2.show()

In [41]:
x_min = 0.5
x_max = 2
x_num = 10000

RC = 0.007
n = 501
amplitude = 5
scatterplot3 = ScatterPlot(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
RC = 0.1
scatterplot3.add_trace(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
"""
RC *= 10
scatterplot2.add_trace(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
"""
scatterplot3.update_layout(title_text = r'$V_{TRIG} \text{ vs Time Graph}$', x_lab = 't(s)', y_lab = '$V_{TRIG} (V)$')
scatterplot3.show()

In [42]:
x_min = 4
x_max = 5
x_num = 10000

RC = 0.007
n = 501
amplitude = 5
scatterplot4 = ScatterPlot(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
RC = 0.1
scatterplot4.add_trace(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
"""
RC *= 10
scatterplot2.add_trace(V_trig, x_min, x_max, x_num, show_original = True, mode = 'lines', name = f'RC = {RC}')
"""
scatterplot4.update_layout(title_text = r'$V_{TRIG} \text{ vs Time Graph}$', x_lab = 't(s)', y_lab = '$V_{TRIG} (V)$')
scatterplot4.show()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:22: RuntimeWarning:

overflow encountered in exp

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:22: RuntimeWarning:

overflow encountered in multiply

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:26: RuntimeWarning:

overflow encountered in exp



In [43]:
# test the differentiator and integrator with an identity function
def identity(x):
  """
  diff = Differentiation(x = x, y = pulse(x))
  integ = Integration(x = x, y = diff.diff_y)
  return integ.int_y
  """
  integ = Integration(x = x, y = pulse(x))
  diff = Differentiation(x = x, y = integ.int_y)
  return diff.diff_y
scatterplot3 = ScatterPlot(identity, x_min, x_max, x_num, show_original = True, mode = 'lines')
scatterplot3.show()

In [44]:
L_ref = 3
def L_ref_line(x):
  return np.zeros_like(x) + L_ref

C_ref = 1
def C_ref_line(x):
  return np.zeros_like(x) + C_ref

In [47]:
#basic RC circuit graphing
x_min = 0
x_max = 6
x_num = 1000
Vcc = 5
RC = (10000 + 100) * 100e-6


def RC_discharge(x):
  return Vcc * (1 - np.exp(-x/RC))

scatterplot = ScatterPlot(RC_discharge, x_min, x_max, x_num, show_original = True, mode = 'lines', name = 'Discharging')
scatterplot.add_trace(C_ref_line, x_min, x_max, x_num, show_original = True, mode = 'lines', name = r'$C_{ref}$')
scatterplot.add_trace(L_ref_line, x_min, x_max, x_num, show_original = True, mode = 'lines', name = r'$L_{ref}$')
scatterplot.update_layout(x_lab = 't(s)', y_lab = r'$V_B (V)$', title_text = 'RC Charging Plot')
scatterplot.show()

In [48]:
x_min = 0
x_max = 0.06
x_num = 1000
Vcc = 5
RC = 100 * 100e-6

def RC_charge(x):
  return Vcc * np.exp(-x/RC)

scatterplot = ScatterPlot(RC_charge, x_min, x_max, x_num, show_original = True, mode = 'lines', name = 'Charging')
scatterplot.add_trace(C_ref_line, x_min, x_max, x_num, show_original = True, mode = 'lines', name = r'$C_{ref}$')
scatterplot.add_trace(L_ref_line, x_min, x_max, x_num, show_original = True, mode = 'lines', name = r'$L_{ref}$')
scatterplot.update_layout(x_lab = 't(s)', y_lab = r'$V_B (V)$', title_text = 'RC Discharging Plot')
scatterplot.show()

In [4]:
def fatr(n):
  yield n
  yield fatr(n+1)
k = fatr(2)

In [7]:
next(k)

StopIteration: ignored